In [4]:
#    This file is part of EAP.
#
#    EAP is free software: you can redistribute it and/or modify
#    it under the terms of the GNU Lesser General Public License as
#    published by the Free Software Foundation, either version 3 of
#    the License, or (at your option) any later version.
#
#    EAP is distributed in the hope that it will be useful,
#    but WITHOUT ANY WARRANTY; without even the implied warranty of
#    MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE. See the
#    GNU Lesser General Public License for more details.
#
#    You should have received a copy of the GNU Lesser General Public
#    License along with EAP. If not, see <http://www.gnu.org/licenses/>.


import random
import array

import numpy

from itertools import chain

from deap import base
from deap import benchmarks
from deap import creator
from deap import tools

# Problem dimension
NDIM = 10

creator.create("FitnessMin", base.Fitness, weights=(-1.0,))
creator.create("Individual", array.array, typecode='d', fitness=creator.FitnessMin)

def mutDE(y, a, b, c, f):
    size = len(y)
    for i in range(len(y)):
        y[i] = a[i] + f*(b[i]-c[i])
    return y

def cxBinomial(x, y, cr):
    size = len(x)
    index = random.randrange(size)
    for i in range(size):
        if i == index or random.random() < cr:
            x[i] = y[i]
    return x

def cxExponential(x, y, cr):
    size = len(x)
    index = random.randrange(size)
    # Loop on the indices index -> end, then on 0 -> index
    for i in chain(range(index, size), range(0, index)):
        x[i] = y[i]
        if random.random() < cr:
            break
    return x

toolbox = base.Toolbox()
toolbox.register("attr_float", random.uniform, -3, 3)
toolbox.register("individual", tools.initRepeat, creator.Individual, toolbox.attr_float, NDIM)
toolbox.register("population", tools.initRepeat, list, toolbox.individual)
toolbox.register("mutate", mutDE, f=0.8)
toolbox.register("mate", cxExponential, cr=0.8)
toolbox.register("select", tools.selRandom, k=3)
toolbox.register("evaluate", benchmarks.griewank)

def main():
    # Differential evolution parameters
    MU = NDIM * 10
    NGEN = 200    
    
    pop = toolbox.population(n=MU);
    hof = tools.HallOfFame(1)
    stats = tools.Statistics(lambda ind: ind.fitness.values)
    stats.register("avg", numpy.mean)
    stats.register("std", numpy.std)
    stats.register("min", numpy.min)
    stats.register("max", numpy.max)
    
    logbook = tools.Logbook()
    logbook.header = "gen", "evals", "std", "min", "avg", "max"
    
    # Evaluate the individuals
    fitnesses = toolbox.map(toolbox.evaluate, pop)
    for ind, fit in zip(pop, fitnesses):
        ind.fitness.values = fit
    
    record = stats.compile(pop)
    logbook.record(gen=0, evals=len(pop), **record)
    print(logbook.stream)

    for g in range(1, NGEN):
        children = []
        for agent in pop:
            # We must clone everything to ensure independance
            a, b, c = [toolbox.clone(ind) for ind in toolbox.select(pop)]
            x = toolbox.clone(agent)
            print("x=",x)
            y = toolbox.clone(agent)
            
            y = toolbox.mutate(y, a, b, c)
            print("y=",y)
            z = toolbox.mate(x, y)
            print("z=",z)
            del z.fitness.values
            children.append(z)
            
        fitnesses = toolbox.map(toolbox.evaluate, children)
        for (i, ind), fit in zip(enumerate(children), fitnesses):
            ind.fitness.values = fit
            if ind.fitness > pop[i].fitness:
                pop[i] = ind
        
        hof.update(pop)
        record = stats.compile(pop)
        logbook.record(gen=g, evals=len(pop), **record)
        print(logbook.stream)
    
    print("Best individual is ", hof[0])
    print("with fitness", hof[0].fitness.values[0])
    return logbook
            
if __name__ == "__main__":
    main()

gen	evals	std      	min     	avg    	max    
0  	100  	0.0676406	0.766409	1.00361	1.24636
x= Individual('d', [-0.4756620174377231, -1.399487552902563, 2.2252703724039513, -2.084345787382736, 2.8349874035371156, 1.4887961901566031, 2.060299669067229, -1.7336574420420918, 1.1106212586316033, -0.8768846753247619])
y= Individual('d', [0.04785005405046405, -1.1033827054082441, -0.8681674516860842, -4.5536547041857816, 0.01703956252524108, 2.782666402348793, 0.02645583542978225, -2.4490717093275385, -1.2294644965852446, 0.8291448422801204])
z= Individual('d', [-0.4756620174377231, -1.399487552902563, 2.2252703724039513, -2.084345787382736, 2.8349874035371156, 1.4887961901566031, 2.060299669067229, -2.4490717093275385, 1.1106212586316033, -0.8768846753247619])
x= Individual('d', [-1.727376755555288, -1.517765809051357, -2.982046207670108, -1.695786647025587, -0.09064853178961663, -0.5236930646991969, -2.890928443579848, -2.9399832395294707, 0.05891811761601318, 0.009849942499361664])
y= Indiv

x= Individual('d', [1.9552623642679006, 1.271164969997507, 0.4465267288409347, 2.4393476668677483, -1.0200593958654427, -2.253739493762456, 2.1964678729839333, -2.861635124433099, 1.420193838525285, -2.5008534035622176])
y= Individual('d', [-3.4369323089457215, 2.4511298375400843, 2.185265484614045, 4.576712200257461, 3.4420546970978547, 0.2711515279171026, -1.1264802291307592, -4.080467769435296, 3.3198678119101723, -0.8904380632666409])
z= Individual('d', [-3.4369323089457215, 2.4511298375400843, 0.4465267288409347, 2.4393476668677483, -1.0200593958654427, -2.253739493762456, 2.1964678729839333, -2.861635124433099, 1.420193838525285, -2.5008534035622176])
x= Individual('d', [0.3617725473861917, 1.7881954445050345, 2.2062497878017506, 1.8760470796647102, -2.1305407645607426, 0.6801357617105497, -2.5463356994541497, -1.8181619283456298, 0.8128755647257657, 2.2887331961252055])
y= Individual('d', [-1.096497912600425, -2.8451318987613337, -3.5077328719478826, 3.2171518657628746, -0.92212

x= Individual('d', [0.8683486697076623, -0.17460992957230026, -1.4859343608630058, -1.121559609909239, -2.501770317784743, -1.5535515535369702, -1.8952978210189728, -2.903601681935954, -1.8884704876934353, -1.7851909951452174])
y= Individual('d', [-0.2991611316481029, 0.7726990513572041, 1.9123367579062371, -0.07171027363228344, 0.15149343098541923, 2.032740852286761, -3.2706548787737635, 3.404474846865355, 2.4471648589283657, 5.535682940595364])
z= Individual('d', [0.8683486697076623, -0.17460992957230026, -1.4859343608630058, -1.121559609909239, -2.501770317784743, -1.5535515535369702, -1.8952978210189728, -2.903601681935954, 2.4471648589283657, -1.7851909951452174])
x= Individual('d', [0.3303015649718226, -2.676406556333884, -0.6442741573376582, 0.4822490667635684, 2.2497181505285377, -0.1755384102628057, -5.289081514917548, 2.3326283324418737, -1.1613833886686729, -2.9975071538891367])
y= Individual('d', [-0.04641569427441139, -1.438359173397304, 1.3102585789037953, 4.5225569378514

x= Individual('d', [-0.5598040313426509, 1.9501735094457926, -0.4255994138207724, -0.5708766153168865, 1.3301720515239097, 2.0046315815716333, -0.7168851586840828, 1.6524941582109545, -1.6309312767586586, 2.9572151349771003])
y= Individual('d', [-0.705714363124613, -0.9689789705853455, 3.774724163708245, 5.5371681164211, -1.867249878482377, 0.19753193013424486, -0.66686497092341, 2.9574851082790437, 2.2739279760544426, 1.8015999802014928])
z= Individual('d', [-0.5598040313426509, 1.9501735094457926, -0.4255994138207724, -0.5708766153168865, 1.3301720515239097, 0.19753193013424486, -0.66686497092341, 1.6524941582109545, -1.6309312767586586, 2.9572151349771003])
x= Individual('d', [-0.5442985082315364, -1.2238747237745458, -2.691905231198573, 2.4795030276749372, 0.2220498319761175, 1.2198197209579091, -2.2902126273249817, -0.47798923521136505, 0.7270979858225681, -0.6850029251386585])
y= Individual('d', [-5.003965729166536, 3.7030608754166066, 3.791786159665888, -1.6309774178867853, -1.3

y= Individual('d', [-4.3741985986972605, 2.034191171163893, 0.21919730495729994, 6.07019010730313, -0.34428021652810026, 0.372138071764348, -0.6743193824031091, -6.040585127905123, 1.1443968136154532, -4.2483325514253005])
z= Individual('d', [1.5865290811632153, 1.468377529622372, -3.6253109386203977, 0.14819792594284964, -0.9871450621863862, 0.372138071764348, -0.1641519846459052, 2.79633405928298, 0.1270257433310138, -0.061266241364304364])
x= Individual('d', [-0.4166532292976233, -0.4188036736232572, 0.28948024038954046, -1.1655300861683369, 1.0440956289703642, 0.8278592296919003, 0.3301048817470731, 2.4373684983457213, 0.27370091807371466, -0.050124575429952856])
y= Individual('d', [1.1001842365983627, 2.924967482462775, -6.062643765104022, -0.26584616202019185, -5.567864442703623, 2.1477737330992, 1.2161309856910048, 0.1527665911495406, -0.5760258805660784, 1.2110327726499406])
z= Individual('d', [-0.4166532292976233, 2.924967482462775, 0.28948024038954046, -1.1655300861683369, 1.

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Individual('d', [0.352834006910137, 0.050437545717081034, 0.00835611339875948, -0.0034791523840369777, 0.0006948428626691715, 0.0005265490506605644, 0.002338120464614244, -0.0008428358490446188, -0.0009035679889623163, -0.0012475809945658946])
x= Individual('d', [-3.1841142554066435, 0.21272005563469748, 0.029230485053784797, -0.0005668030596957495, -5.40281503239736, -0.004024085139306421, -0.002825668702643225, 0.0011249616058704396, 0.0010220011677096697, 0.0004375703088210156])
y= Individual('d', [2.288897976160373, 3.583544715790877, -0.006055017421968704, -0.002043738127144908, -0.009034646415529741, 0.0032241349311444767, -0.0009360015847604179, 0.004211275697646772, -0.0024154550395474976, -0.0035322081166274002])
z= Individual('d', [-3.1841142554066435, 0.21272005563469748, 0.029230485053784797, -0.0005668030596957495, -5.40281503239736, 0.0032241349311444767, -0.002825668702643225, 0.0011249616058704396, 0.0010220011677096697, 0.0004375703088210156])
x= Individual('d', [0.090

z= Individual('d', [-0.08405996156020501, 0.07915636665034242, 0.01676079568442701, -0.0009191410485250258, 0.009146611344178258, 0.000373680858976308, 0.0022382928121890966, -0.0008895501853077733, 0.0002991402611915461, 0.004616541222556823])
x= Individual('d', [3.2909659231455226, -4.737863020953835, 0.022186393413263325, -0.007324954462961615, -0.0004090361262530217, 0.0004001035225275544, 0.0009442433556023147, -0.0005540141563092123, 0.000990282269959463, -7.356752018648355e-05])
y= Individual('d', [0.08587358845662557, -4.1719792951452686, -0.019076521274773533, -0.017085739685562054, -4.6441789145615715, -0.004578011772709249, -0.004171469345416221, -0.0027878817941670827, -0.008428078753483108, -0.0006723186194687569])
z= Individual('d', [0.08587358845662557, -4.737863020953835, 0.022186393413263325, -0.007324954462961615, -0.0004090361262530217, 0.0004001035225275544, 0.0009442433556023147, -0.0005540141563092123, 0.000990282269959463, -0.0006723186194687569])
x= Individual('

x= Individual('d', [3.262415417501622, -4.798270871199053, 0.022711501143320826, 0.006439040353614863, 0.004251954330067625, 0.0069522080717915056, 0.001495164899206436, -0.00026272111211180296, 0.00087296506948511, -0.0010353536382407902])
y= Individual('d', [3.4899147555340893, -4.013664964515121, -0.016852597568525744, -0.0023741875865001, 0.011438742643070566, -0.00040985625356026426, 0.0010147788949285697, -0.002768330359944274, 0.00015895111245112442, 0.005249422813144897])
z= Individual('d', [3.262415417501622, -4.798270871199053, 0.022711501143320826, 0.006439040353614863, 0.004251954330067625, 0.0069522080717915056, 0.001495164899206436, -0.002768330359944274, 0.00015895111245112442, -0.0010353536382407902])
x= Individual('d', [0.12804906660770418, 0.3040216595747005, -0.005645142261199914, 0.001169796216474641, 0.007115230149589251, -0.004738697882927795, 0.0014443878600532613, -0.005238871651202407, 0.013449653290857878, -0.0013975463496444934])
y= Individual('d', [2.3072120

x= Individual('d', [3.093613840407433, 0.24205215546805903, 0.035470785878938996, 0.00325501522643123, -4.753828619293849, -0.002036252209285697, 0.00348279438932977, -0.00035268429012107194, -0.0025067611896957445, -0.0010671821435767784])
y= Individual('d', [-3.1698128980534435, 7.646521216224734, 0.024736868388014924, -0.003134776834535135, -4.655396456431598, 0.003129059893724771, 0.0045366448108032685, -0.0022076390504138423, -0.002017887662618383, 0.003051519414410535])
z= Individual('d', [3.093613840407433, 0.24205215546805903, 0.035470785878938996, 0.00325501522643123, -4.655396456431598, -0.002036252209285697, 0.00348279438932977, -0.00035268429012107194, -0.0025067611896957445, -0.0010671821435767784])
x= Individual('d', [3.2234365252156163, 4.280022530350714, -0.009825319608223713, 0.0199159792566058, -0.005949206646563402, -0.0003942923817258307, -0.00039120078064911764, 0.003587357979107866, 0.0005356033343719498, -0.0025313430704442695])
y= Individual('d', [0.398875020465